In [1]:

from __future__ import division
from __future__ import print_function
from __future__ import absolute_import
from distutils.version import StrictVersion
import pytesseract
import shutil
import requests
from decimal import Decimal
import tensorflow as tf
from pathlib import Path
import shapely
import geopandas as gpd
import json
import io
from object_detection.utils import dataset_util, ops
from PIL import Image
import re
from datetime import datetime
import pandas as pd
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '2'    # Suppress TensorFlow logging (1)
import inflect
import cv2
from PIL import Image
import imagehash
import uuid
from shapely.geometry import Polygon
from mining_pages_utils.image_ocr_utils import double_to_singlepage, load_page, cut_image, ocr_pre_processing_page, ocr_pre_processing_figure, ocr_post_processing_pageid, cut_image_savetemp, cut_image_figure, ocr_post_processing_figid
from mining_pages_utils.dataframe_utils import get_page_labelmap_as_df, get_figid_labelmap_as_df, extract_page_detections, extract_page_detections_new,unfold_pagedetections, page_detections_toframe, extract_detections_figureidv2,humanreadID
from mining_pages_utils.dataframe_utils import extract_pdfid, filter_best_page_detections, select_pdfpages, choose_pageid, filter_best_vesselprofile_detections, merge_info,  provide_pagelist, provide_pdf_path, get_pubs_and_configs, pdf_to_imagev2, handleduplicate_humanreadID
from mining_pages_utils.json_utils import create_find_JSONL, create_constructivisttype_JSONL, create_normativtype_JSONL, create_drawing_JSONL, create_catalog_JSONL, create_trench_JSONL
from mining_pages_utils.tensorflow_utils import create_tf_example_new, create_tf_figid, run_inference_for_page_series, run_inference_for_figure_series, build_detectfn, Df2TFrecord, split
from mining_pages_utils.request_utils import getZenonInfo, getZenonBibtex, getAllDocs, DocsStructure, selectOfResourceTypes

if StrictVersion(tf.version.VERSION) < StrictVersion('2.3.0'):
    raise ImportError(
        'Please upgrade your TensorFlow installation to v2.3.* or later!')

tf.get_logger().setLevel('ERROR')           # Suppress TensorFlow logging (2)

# Enable GPU dynamic memory allocation
gpus = tf.config.experimental.list_physical_devices('GPU')
for gpu in gpus:
    tf.config.experimental.set_memory_growth(gpu, True)

INPUTDIRECTORY = '/home/images/apply' 
GRAPH = '/frozen_inference_graph.pb'
LABELS = '/label_map.pbtxt'
PAGE_MODEL = '/home/models/faster_rcnn_resnet50_v1_800x1333_coco17_gpu-8_miningpagesv12'
SAVEDMODEL = '/saved_model'
FIGID_MODEL = '/home/models/faster_rcnn_resnet50_v1_800x1333_coco17_gpu-8_miningfiguresv5_OCKquickv3'
SEG_MODEL = '/home/models/shape_segmentation/train_colab_20200610.h5'
OUTPATH = '/home/images/OUTPUT/'
VESSELLPATH = OUTPATH + 'vesselprofiles/'
SEGMENTPATH = OUTPATH + 'segmented_profiles/'
CSVOUT = OUTPATH + 'mining_pages_allinfo.csv'
CLEANCSVOUT = OUTPATH + 'mining_pages_clean.csv'









Segmentation Models: using `tf.keras` framework.


In [2]:
publist = get_pubs_and_configs(INPUTDIRECTORY)
publist = publist.apply(getZenonInfo, axis=1)
publist = publist.apply(getZenonBibtex, axis=1)
pdflist = provide_pdf_path(publist)
pdflistv2 = pdflist.apply(pdf_to_imagev2, axis=1)
print('Finished pdf2images')
pagelist = provide_pagelist(pdflistv2)
print('Created primary pagelist')
pagelist = pagelist.apply(extract_pdfid, axis=1)
double_to_singlepage(pagelist)
pagelist = provide_pagelist(pdflistv2)
pagelist = pagelist.apply(extract_pdfid, axis=1)
#pagelist = select_pdfpages(pagelist)





For pub_key: ZenonID found pub_info!
@Book{
000066595,
author = {Oxé, August 1863-1944.},
title = {Corpus vasorum Arretinorum},
subtitle = {A catalogue of the signatures, shapes, and chronology of Italian Sigillata},
series = {Antiquitas. Abhandlungen zur Vor- und Frühgeschichte, zur klassischen und provinzial-römischen Archäologie und zur Geschichte des Altertums},
number = {Bd. 41},
editor = {Comfort, Howard, 1904- and Kenrick, Philip M},
location = {Bonn},
publisher = {R. Habelt},
year = {2000},
edition = {2nd ed. /},
crossref = {https://zenon.dainst.org/Record/000066595},
url = {https://zenon.dainst.org/Record/000066595},
urldate ={2021-05-06},
language = {english},
}


[1] August 1863-1944. Oxé. Corpus vasorum Arretinorum. Number Bd. 41 in Antiquitas. Abhandlungen zur Vor- und Frühgeschichte, zur klassischen und provinzial-römischen Archäologie und zur Geschichte des Altertums. R. Habelt, 2nd ed. / edition, 2000. URL: https://zenon.dainst.org/Record/000066595 (visited on 2021-05-0

In [3]:

for path in [VESSELLPATH, SEGMENTPATH]:
    if not os.path.exists(path):
        os.makedirs(path)







all_detections_step1 = pd.DataFrame()
miningpagesdetectfn = build_detectfn(PAGE_MODEL + SAVEDMODEL)
for index, row in pagelist.iterrows():
    print('Page ' + os.path.basename(row['page_path']))

    row, page_imgnp = load_page(row)
    input_tensor = tf.convert_to_tensor(page_imgnp)
    input_tensor = input_tensor[tf.newaxis, ...]
    detections = miningpagesdetectfn(input_tensor)
    del page_imgnp
    del input_tensor
    num_detections = int(detections.pop('num_detections'))
    detections = {key: value[0, :num_detections].numpy()
                   for key, value in detections.items()}
    detections['num_detections'] = num_detections
    row['page_detections']= detections
    all_detections_step1 = all_detections_step1.append(row)










Loading model...Done! Took 6.878658056259155 seconds
Page ock_all.pdf0001-4.png
/home/images/apply/ZenonID_000066595/ock_all.pdf0001-4.png
Page ock_all.pdf0001-3.png
/home/images/apply/ZenonID_000066595/ock_all.pdf0001-3.png
Page ock_all.pdf0002-6.png
/home/images/apply/ZenonID_000066595/ock_all.pdf0002-6.png
Page ock_all.pdf0002-5.png
/home/images/apply/ZenonID_000066595/ock_all.pdf0002-5.png


In [4]:
#all_detections_step2, keylist =unfold_pagedetections(all_detections_step1)
#all_detections_step22 = extract_page_detections(all_detections_step2, keylist, category_index=get_page_labelmap_as_df(PAGE_MODEL + LABELS))
all_detections_step2 = page_detections_toframe(all_detections_step1).drop(columns='page_detections')

page_category_index = get_page_labelmap_as_df(PAGE_MODEL + LABELS)
all_detections_step2 = all_detections_step2.merge(page_category_index, on=['detection_classes'], how='left')

In [5]:
pageids = filter_best_page_detections(all_detections_step2 , lowest_score=0.8)
bestpages = choose_pageid(pageids)
pageid_raw = pd.DataFrame()

#perform ocr page number
for index, row in bestpages.iterrows():
    img = cut_image(row)
    img2 = ocr_pre_processing_page(img)
    result = pytesseract.image_to_string(img2, config=row['pageid_config'])
    row['newinfo'] = result
    
    pageid_raw = pageid_raw.append(row)
all_detections_step3 = merge_info(all_detections_step2, pageid_raw)
all_detections_step3 = all_detections_step3.apply(ocr_post_processing_pageid, axis=1)

figures = filter_best_vesselprofile_detections(all_detections_step3, lowest_score= 0.8)

['pageid']


In [6]:
for index, row in figures.iterrows():
    print(row['detection_scores'])

0.9999973773956299
0.9999967813491821
0.9999943971633911
0.9999938011169434
0.9999936819076538
0.9999923706054688
0.9999914169311523
0.9999873638153076
0.9999871253967285
0.9999862909317017
0.9999853372573853
0.9999850988388062
0.9999842643737793
0.9999839067459106
0.9999827146530151
0.9999818801879883
0.9999790191650391
0.9999781847000122
0.9999762773513794
0.9999728202819824
0.9999717473983765
0.9999631643295288
0.9999607801437378
0.9999556541442871
0.9999514818191528
0.9999480247497559
0.9999469518661499
0.9999344348907471
0.999931812286377
0.9998993873596191
0.8271000385284424
0.9999955892562866
0.999994158744812
0.9999939203262329
0.9999939203262329
0.999992847442627
0.9999915361404419
0.9999912977218628
0.9999904632568359
0.9999880790710449
0.9999874830245972
0.9999871253967285
0.9999860525131226
0.9999856948852539
0.9999849796295166
0.9999828338623047
0.9999796152114868
0.999976396560669
0.9999752044677734
0.9999717473983765
0.9999717473983765
0.9999663829803467
0.99995720386505

In [7]:
#detect figure id


figures_step1 = pd.DataFrame()
figure_category_index = get_figid_labelmap_as_df(FIGID_MODEL + LABELS)
miningfiguresdetectfn = build_detectfn(FIGID_MODEL + SAVEDMODEL)

for index, row in figures.iterrows():
    print('Figure from ' + os.path.basename(row['page_path']))
    row, figure_imgnp = cut_image_savetemp(row, VESSELLPATH)
    input_tensor = tf.convert_to_tensor(figure_imgnp)
    input_tensor = input_tensor[tf.newaxis, ...]
    detections = miningfiguresdetectfn(input_tensor)
    del figure_imgnp
    del input_tensor
    num_detections = int(detections.pop('num_detections'))
    print(num_detections)
    print(detections)
    #print(type(detections['detection_multiclass_scores']))
    detectionsDL = { key: value[0, :num_detections].numpy()
                   for key, value in detections.items()}
    #print(detectionsDL)
    detectionsDL['detection_classesname'] = [ figure_category_index.loc[figure_category_index['figid_detection_classes'] == i, 'figid_detection_classesname'].item() for i in detectionsDL['detection_classes'] ]
    detectionsLD = [{key : value[i] for key, value in detectionsDL.items()} 
         for i in range(num_detections)] 
    #print(detectionsLD)
    row['figure_detections'] = detectionsLD
    #print(row['figure_detections'][0]['detection_scores'])
    row['figure_num_detections'] = num_detections       
    figures_step1 = figures_step1.append(row)

#figid_category_index = get_figid_labelmap_as_df(PAGE_MODEL + LABELS)
#figures_step2 = 
#figure_detections_names = [detection['detection_classes'] :  for detection in figures_step1['figure_detections']]

#figures_step1['figure_detections'].merge(
#figid_category_index, on=['figid_detection_classes'], how='left')






Loading model...Done! Took 7.865797281265259 seconds
Figure from ock_all.pdf0001-4.png
100
{'detection_classes': <tf.Tensor: shape=(1, 100), dtype=float32, numpy=
array([[3., 2., 2., 3., 4., 1., 4., 1., 1., 4., 4., 3., 4., 4., 2., 2.,
        2., 3., 2., 1., 3., 2., 2., 2., 4., 2., 2., 3., 2., 2., 4., 2.,
        4., 4., 3., 4., 3., 1., 3., 3., 2., 3., 3., 2., 1., 2., 2., 4.,
        2., 3., 3., 2., 3., 3., 3., 2., 4., 4., 3., 4., 4., 4., 3., 4.,
        3., 2., 3., 3., 4., 2., 4., 1., 1., 3., 2., 2., 4., 4., 4., 4.,
        3., 4., 4., 4., 2., 2., 4., 4., 3., 1., 1., 1., 3., 2., 1., 3.,
        1., 1., 4., 4.]], dtype=float32)>, 'detection_multiclass_scores': <tf.Tensor: shape=(1, 100, 5), dtype=float32, numpy=
array([[[6.21591994e-07, 1.00019371e-08, 7.49192985e-10, 9.99999404e-01,
         1.34518771e-10],
        [1.24965220e-06, 1.61630815e-08, 9.99998450e-01, 2.69538617e-07,
         7.43339701e-09],
        [7.72369802e-01, 7.48236289e-06, 3.51391325e-04, 2.27184653e-01,
       

In [8]:

def filterFigureDetections(series):
    if series['frame_contains']:
        if series['detection_classesname'] in series['allowedFrameDetections']:
            detections = [i for i in series['figure_detections'] if i['detection_classesname'] in series['frame_contains']]
            #print(detections)
            detections_df = pd.DataFrame(detections)
            detections_df = detections_df[detections_df['detection_scores'] == detections_df.groupby('detection_classesname')['detection_scores'].transform('max')]
            series['bestfigure_detections'] = detections_df.to_dict('records')
    if series['figure_contains'] :
        if series['detection_classesname'] in series['allowedFigureDetections'] :
            detections = [i for i in series['figure_detections'] if i['detection_classesname'] in series['figure_contains']]
            detections_df = pd.DataFrame(detections)
            print(detections_df)
            detections_df = detections_df[detections_df['detection_scores'] == detections_df.groupby('detection_classesname')['detection_scores'].transform('max')]
            #detectionsmax = detections_df.groupby(['detection_classesname'], sort=False)['detection_scores'].max()
            #df['count_max'] = df.groupby(['Mt'])['count'].transform(max)
            #detections_dfmax = detections_df[detections_df['detection_scores'] == detections_df.groupby('detection_classesname')['detection_scores'].transform('max')]
            print(detections_df)
            series['bestfigure_detections'] = detections_df.to_dict('records')
    return series


figures_step2 = figures_step1.apply(filterFigureDetections, axis=1)
#for index, row in figures_step2.iterrows():
    #print(row['figure_path'])
    #if type(row['bestfigure_detections']) == list:
        #for i in row['bestfigure_detections']:
            #print(i['detection_classesname'], i['detection_scores'])




    detection_classes                        detection_multiclass_scores  \
0                 3.0  [6.21592e-07, 1.0001937e-08, 7.49193e-10, 0.99...   
1                 2.0  [1.2496522e-06, 1.6163082e-08, 0.99999845, 2.6...   
2                 2.0  [0.7723698, 7.482363e-06, 0.00035139133, 0.227...   
3                 3.0  [0.03832807, 2.7326658e-05, 0.961384, 0.000254...   
4                 3.0  [0.9999999, 9.579519e-09, 1.9703155e-08, 1.535...   
5                 2.0  [1.0, 8.810763e-11, 3.049689e-08, 1.6962197e-0...   
6                 2.0  [0.9999999, 9.579519e-09, 1.9703155e-08, 1.535...   
7                 2.0  [1.0, 1.0207577e-09, 1.795934e-08, 5.1649356e-...   
8                 3.0  [1.0, 8.810763e-11, 3.049689e-08, 1.6962197e-0...   
9                 2.0  [1.0, 3.0129918e-12, 1.26685045e-08, 5.6566757...   
10                3.0  [1.0, 4.9864607e-10, 6.749786e-09, 5.8421215e-...   
11                2.0  [1.0, 8.4945505e-12, 5.5217857e-09, 3.7830436e...   
12          

In [9]:
#perform ocr figid

def ocr_post_processing_figure(row, detection):
    print(detection['detection_classesname'])
    if row[str(detection['detection_classesname']) + '_raw']:
        print(detection['detection_classesname'])
        print (row[str(detection['detection_classesname']) + '_raw'])
        if str(detection['detection_classesname']) + '_exclude_strings' in list(row.keys()):
            for exclude_string in row[str(detection['detection_classesname']) + '_exclude_strings']:
                row[str(detection['detection_classesname']) + '_raw'].replace(exclude_string,"")
        else:
            print(str(detection['detection_classesname']) + '_exclude_strings' + ' not written in config - No strings will be excluded.')
        #print(str(detection['detection_classesname']))
        if str(detection['detection_classesname']) + '_regex' in list(row.keys()):
            #print(str(detection['detection_classesname']) + '_regex')
            regex = re.compile(row[str(detection['detection_classesname']) + '_regex'])
            result = re.search(regex, row[str(detection['detection_classesname']) + '_raw'])
            if result:
                row[str(detection['detection_classesname']) + '_clean'] = result.group(1)

        else:
            print(str(detection['detection_classesname']) + '_regex' + ' not written in config - No regex filter will be applied')

    return row

def ocr_post_processing_textall(row):
    
    textall_regex = re.compile(row['textall_regex'])
    result = re.search(textall_regex, row['textall_raw'])
    if result:
        row['textall_clean'] = result.group(1)
    else:
        row['textall_clean'] = 'none'

    return row


figures_step3 = pd.DataFrame()
for index, row in figures_step2.iterrows():
    #print('OCR ' + os.path.basename(row['figure_path']))
    figure_imgnp = cv2.imread(row['figure_path'])
    figure_imgnp = ocr_pre_processing_page(figure_imgnp)
    row['textall_raw'] = pytesseract.image_to_string(figure_imgnp, config=row['textall_config'])
    del figure_imgnp
    row = ocr_post_processing_textall(row)
    detections = []
    if type(row['bestfigure_detections']) == list:
        for detection in row['bestfigure_detections']:
            detection = cut_image_figure(row, detection)
            detection = ocr_pre_processing_figure(detection)
            #print(detection['detection_classesname'])
            if str(detection['detection_classesname']) + '_config' in list(row.keys()):
                row[str(detection['detection_classesname']) + '_raw'] = pytesseract.image_to_string(detection['imgnp'], config=row[str(detection['detection_classesname']) + '_config'])
                del detection['imgnp']
                #print(row[str(detection['detection_classesname']) + '_raw'])
            else:
                row[str(detection['detection_classesname']) + '_raw'] = pytesseract.image_to_string(detection['imgnp'], config=row['pageid_config'])
                #print(row[str(detection['detection_classesname']) + '_raw'])
            row['figure_detections'] = detections.append(detection)
            row = ocr_post_processing_figure(row, detection)
        
        

    figures_step3 = figures_step3.append(row)
print(figures_step3['figureid_clean'])





figureinfo
figureinfo
2079]

figureid
figureid
1*

figureinfo
figureinfo
16 SO4

figureid
figureid
2

infoframeid
infoframeid
25

figureinfo
figureinfo
15 264
Scale?

figureid
figureid
1

infoframeid
infoframeid
20

figureid
figureid
1°

figureinfo
figureinfo
17.575

infoframeid
infoframeid
19

figureinfo
figureinfo
20792

figureid
figureid
2"

infoframeid
infoframeid
a1

figureid
figureid
1

figureinfo
figureinfo
19612

figureid
figureid
2

figureinfo
figureinfo
19 694.6

figureinfo
figureinfo
16377

figureid
figureid
5

figureinfo
figureinfo
20 776

figureid
figureid
1

infoframeid
infoframeid
23

figureinfo
figureinfo
17 423

figureid
figureid
1

figureid
figureid
1"

figureinfo
figureinfo
20 785

infoframeid
infoframeid
24

figureid
figureid
4"

figureinfo
figureinfo
20 782

figureinfo
figureinfo
20795

figureid
figureid
2

figureinfo
figureinfo
20 781

figureid
figureid
2°

figureinfo
figureinfo
20 789

figureid
figureid
3

figureid
figureid
4"


In [10]:
def generateShapebox(series):
    box = series['detection_boxes']
    ymin, xmin, ymax, xmax = box
    bbox_xmin = int((xmin)*series['page_width'])
    bbox_ymin = int((ymin)*series['page_height'])
    bbox_xmax = int((xmax)*series['page_width'])
    bbox_ymax = int((ymax)*series['page_height'])
    shapebox = shapely.geometry.box(bbox_xmin, bbox_ymin, bbox_xmax, bbox_ymax, ccw=True)
    series['detection_shapebox'] = shapebox
    return series
def seperateFramesFigures(group):
    infoframes = group[group['detection_classesname'] == 'infoframe']
    figures = group[group['detection_classesname'] != 'infoframe']
    #print(infoframes)
    figuresWithInfo = figures.apply(infosFromFrames, infoframes=infoframes, axis=1)
    return figuresWithInfo


def infosFromFrames(series, infoframes):
    for index, row in infoframes.iterrows():
        if series['detection_shapebox'].within(row['detection_shapebox']):
            for info in row['frame_contains']:
                if info + '_raw' in row.keys():
                #print(row[info + '_raw'])
                    series[info + '_raw'] = row[info + '_raw']
                    series[info + '_clean'] = row[info + '_clean']
    return series

figures_step3 = figures_step3.apply(generateShapebox, axis=1)
figures_geodf = gpd.GeoDataFrame( figures_step3,geometry= 'detection_shapebox')
figures_geodf2 = figures_geodf.groupby('page_path', as_index=False).apply(seperateFramesFigures).reset_index()
#print(figures_geodf2['infoframeid_raw'])
 
    




 

In [11]:




def humanreadID(Series):
    humanreadID = ''
    if Series['patternHRID']:
        for element in Series['patternHRID']:
            if element in list(Series.keys()):
                humanreadID += str(Series[element]) + '_'
            else:
                print('HRID Element: ' + element + ' does not exist.')
                humanreadID += element + '_'
    else:

        humanreadID = str(Series['figure_tmpid'])

    Series['HRID'] = humanreadID.rstrip('_')
    return Series

figures_step4 = figures_geodf2.apply(humanreadID, axis=1)
figures_step4 = handleduplicate_humanreadID(figures_step4)

In [13]:
auth = ('', 'blub')
db_url = 'http://host.docker.internal:3000'
#db_url = 'http://localhost:3000'
###This is a temporal solution as we should group by exportProject and bulksave to pouchdb########
db_name = figures_step4['exportProject'][0]
pouchDB_url_find = f'{db_url}/{db_name}/_find'
pouchDB_url_put = f'{db_url}/{db_name}/'
pouchDB_url_bulk = f'{db_url}/{db_name}/_bulk_docs'
idaifieldconfigpath = Path('/home/idaifieldConfigs')
print(print(cv2.__dict__))

#print(json.dumps(allDocs, indent=4, sort_keys=True))
#categoriesStructureDF = DocsStructure(allDocs)
#print(categoriesStructureDF)

#for index,row in categoriesStructureDF.iterrows():
    #print(index, row)
#groups = categoriesStruc
def findDuplicateImages(df):
    for index,row in df.iterrows():
        hsh = imagehash.average_hash(Image.open(row['figure_imagestorepath']))
        
        #cv2.img_hash_BlockMeanHash.compute(img)
        #hsh = cv2.img_hash.BlockMeanHash_create()
        #hsh.compute(img)
        #phash = cv2.img_hash.pHash(img)
        print(hsh)


    #return duplicates

    # plot duplicates obtained for a given file using the duplicates dictionary
    #from imagededup.utils import plot_duplicates
    #plot_duplicates(image_dir='path/to/image/directory',
                    #duplicate_map=duplicates,
                    #filename='ukbench00120.jpg')

def findExistingIdentifiers(newDOC, oldDOC):
    return sameIdentifierDOC
def bulkSaveChanges(DOC, pouchDB_url_bulk, auth ):
    answer = requests.post(pouchDB_url_bulk , auth=auth, json=DOC)
    return print(answer)
def pageCorrStat(df):
    return pageDistance
def pageCorrection(series):
    return series
def enterCreated(doc):
    now = datetime.now()
    daytoSec = now.strftime('%Y-%m-%dT%H:%M:%S')
    sec = "{:.3f}".format(Decimal(now.strftime('.%f')))
    doc['created'] = {}
    doc['created']['user'] = 'Script mhaibt'
    doc['created']['date'] = daytoSec + str(sec)[1:] + 'Z'
    return doc
def imageToStore(series):
    #print(series)
    series['figure_imagestorepath'] = os.path.join(series['imagestore'], series['exportProject'], os.path.basename(series['figure_path']).replace('.png','') )
    shutil.copyfile(str(series['figure_path']), series['figure_imagestorepath'])
    return series

def createDrawingDocs (series):
    doc = {}
    doc['_id'] = str(series['figure_tmpid'])
    doc['modified'] = []
    doc = enterCreated(doc)
    resource = doc['resource'] = {}
    resource['type'] = 'Drawing'
    resource['identifier'] = series['HRID']
    resource['shortDescription'] =  series['detection_classesname'] + ' ' +series['HRID']
    resource['originalFilename'] = os.path.basename(series['figure_path'])
    resource['width'] = int(series['figure_width'])
    resource['height'] = int(series['figure_height'])
    resource['id'] = str(series['figure_tmpid'])
    resource['description'] = series['textall_raw'] + ' ' + series['pageinfo_raw']
    resource['literature'] = []
    if series['pub_key'] == 'ZenonID':
        resource['literature'].append({'zenonId' : str(series['pub_value']), 'page' : str(series['pageid_clean']) , 'figure' : str(series['figureid_clean']) ,'quotation' : str(series['pub_quote']) })
    doc['resource'] = resource
    return DrawingDocs.append(doc)



DrawingDocs = []
DocHull = {}

figures_step4.apply(createDrawingDocs, axis=1)

allDocs = getAllDocs(auth, pouchDB_url_find)
allDocs = allDocs['docs']
allDocs = [doc for doc in  allDocs if 'type' in doc['resource'].keys()]
existingDrawings = selectOfResourceTypes(['Drawing'], allDocs)
#findExistingIdentifiers(DrawingDocs, existingDrawings)


DocHull['docs'] = DrawingDocs
#print(json.dumps(DrawingDocs, indent=4, sort_keys=True))
#figures_step4.apply(imageToStore)
figures_step5 = figures_step4.apply(imageToStore, axis=1)
findDuplicateImages(figures_step5)

#duplicateimages = findDuplicateImages()
#print(duplicateimages)

#bulkSaveChanges(DocHull, pouchDB_url_bulk, auth )
#print(AllDocs)



    
    

#cleanrow=row[columns].dropna() 
#äprint(cleanrow)
#row['resource']= cleanrow.to_dict()

#with open(OUTPATH + 'catalogs.jsonl', 'w') as f:
    #pubs = figures_step3[['pub_key', 'pub_value']].drop_duplicates()
    #pubs.apply(create_catalog_JSONL, file=f, axis=1)
#with open(OUTPATH + 'trenches.jsonl', 'w') as f:
    #pubs = figures_step3[['pub_key', 'pub_value']].drop_duplicates()
    #pubs.apply(create_trench_JSONL, file=f, axis=1)
#with open(OUTPATH + 'types.jsonl', 'w') as f:
    #figures_step3.apply(create_constructivisttype_JSONL, file=f, axis=1)
#with open(OUTPATH + 'types_standalone.jsonl', 'w') as f:
    #figures_step3.apply(create_normativtype_JSONL, file=f, axis=1)
#with open(OUTPATH + 'finds.jsonl', 'w') as f:
    #figures_step3.apply(create_find_JSONL, file=f, axis=1)
#with open(OUTPATH + 'drawings.jsonl', 'w') as f:
    #figures_step3.apply(create_drawing_JSONL, file=f, axis=1)










#Profile segmentation
#print('Perform image segmentation')
#run_vesselprofile_segmentation(VESSELLPATH, SEGMENTPATH, SEG_MODEL)

{'__name__': 'cv2.cv2', '__doc__': 'Python wrapper for OpenCV.', '__package__': 'cv2', '__loader__': <_frozen_importlib_external.ExtensionFileLoader object at 0x7f5025bc7e10>, '__spec__': ModuleSpec(name='cv2.cv2', loader=<_frozen_importlib_external.ExtensionFileLoader object at 0x7f5025bc7e10>, origin='/usr/local/lib/python3.6/dist-packages/cv2/cv2.cpython-36m-x86_64-linux-gnu.so'), '__path__': ['/usr/local/lib/python3.6/dist-packages/cv2'], '__file__': '/usr/local/lib/python3.6/dist-packages/cv2/cv2.cpython-36m-x86_64-linux-gnu.so', '__cached__': '/usr/local/lib/python3.6/dist-packages/cv2/__pycache__/__init__.cpython-36.pyc', '__builtins__': {'__name__': 'builtins', '__doc__': "Built-in functions, exceptions, and other objects.\n\nNoteworthy: None is the `nil' object; Ellipsis represents `...' in slices.", '__package__': '', '__loader__': <class '_frozen_importlib.BuiltinImporter'>, '__spec__': ModuleSpec(name='builtins', loader=<class '_frozen_importlib.BuiltinImporter'>), '__build

In [ ]:
def createCatalogDocs (series):
    doc = {}
    #doc['_id'] = str(series['figure_tmpid'])
    doc['modified'] = []
    doc = enterCreated(doc)
    resource = doc['resource'] = {}
    resource['type'] = 'Drawing'
    resource['identifier'] = series['HRID']
    resource['shortDescription'] =  series['detection_classesname'] + ' ' +series['HRID']
    resource['originalFilename'] = os.path.basename(series['figure_path'])
    resource['width'] = int(series['figure_width'])
    resource['height'] = int(series['figure_height'])
    resource['id'] = str(series['figure_tmpid'])
    resource['description'] = series['textall_raw'] + ' ' + series['pageinfo_raw']
    resource['literature'] = []
    if series['pub_key'] == 'ZenonID':
        resource['literature'].append({'zenonId' : str(series['pub_value']), 'page' : str(series['pageid_clean']) , 'figure' : str(series['figureid_clean']) ,'quotation' : str(series['pub_quote']) })
    doc['resource'] = resource
    return DrawingDocs.append(doc)

In [ ]:
figures_step4.to_csv(CSVOUT)
#figures_clean = figures_step4[['pub_key','pub_value','figure_tmpid','HRID','detection_scores', 'detection_classesname','page_imgname','pageid_raw','figureid_raw','pageid_clean','figureid_clean', 'infoframeid_clean', 'figureinfo_clean', 'pageinfo_raw','figure_path','page_path']]
#figures_clean.to_csv(CLEANCSVOUT)

In [ ]:
def create_tf_example_new(group, path):
    with tf.io.gfile.GFile(os.path.join(path, '{}'.format(group.filename)), 'rb') as fid:
        encoded_jpg = fid.read()
    encoded_jpg_io = io.BytesIO(encoded_jpg)
    image = Image.open(encoded_jpg_io)
    width, height = image.size
    fileid = os.path.basename(group.filename)
    fileid = fileid.encode('utf8')
    filename = group.filename.encode('utf8')
    image_format = b'png'
    xmins = []
    xmaxs = []
    ymins = []
    ymaxs = []
    classes_text = []
    classes = []

    for index, row in group.object.iterrows():
        box = row['detection_boxes']
        ymin, xmin, ymax, xmax = box
        xmins.append(xmin)
        xmaxs.append(xmax)
        ymins.append(ymin)
        ymaxs.append(ymax)
        classes_text.append(
            row['detection_classesname'].encode('utf8'))
        classes.append(int(row['detection_classes']))
    tf_example = tf.train.Example(features=tf.train.Features(feature={
        'image/height': dataset_util.int64_feature(height),
        'image/width': dataset_util.int64_feature(width),
        'image/filename': dataset_util.bytes_feature(fileid),
        # 'image/source_id': dataset_util.bytes_feature(filename),
        'image/source_id': dataset_util.bytes_feature(fileid),
        'image/encoded': dataset_util.bytes_feature(encoded_jpg),
        'image/format': dataset_util.bytes_feature(image_format),
        'image/object/bbox/xmin': dataset_util.float_list_feature(xmins),
        'image/object/bbox/xmax': dataset_util.float_list_feature(xmaxs),
        'image/object/bbox/ymin': dataset_util.float_list_feature(ymins),
        'image/object/bbox/ymax': dataset_util.float_list_feature(ymaxs),
        'image/object/class/text': dataset_util.bytes_list_feature(classes_text),
        'image/object/class/label': dataset_util.int64_list_feature(classes),
    }))
    return tf_example

def create_tf_example_figure(group, path):
    with tf.io.gfile.GFile(os.path.join(path, '{}'.format(group.filename)), 'rb') as fid:
        encoded_jpg = fid.read()
    encoded_jpg_io = io.BytesIO(encoded_jpg)
    image = Image.open(encoded_jpg_io)
    width, height = image.size
    fileid = os.path.basename(group.filename)
    fileid = fileid.encode('utf8')
    filename = group.filename.encode('utf8')
    image_format = b'png'
    xmins = []
    xmaxs = []
    ymins = []
    ymaxs = []
    classes_text = []
    classes = []

    for index, row in group.object.iterrows():
        if type(row['bestfigure_detections']) == list:
            for detection in row['bestfigure_detections']:
                box = detection['detection_boxes']
                ymin, xmin, ymax, xmax = box
                xmins.append(xmin)
                xmaxs.append(xmax)
                ymins.append(ymin)
                ymaxs.append(ymax)
                classes_text.append(
                    detection['detection_classesname'].encode('utf8'))
                classes.append(int(detection['detection_classes']))
    tf_example = tf.train.Example(features=tf.train.Features(feature={
        'image/height': dataset_util.int64_feature(height),
        'image/width': dataset_util.int64_feature(width),
        'image/filename': dataset_util.bytes_feature(fileid),
        # 'image/source_id': dataset_util.bytes_feature(filename),
        'image/source_id': dataset_util.bytes_feature(fileid),
        'image/encoded': dataset_util.bytes_feature(encoded_jpg),
        'image/format': dataset_util.bytes_feature(image_format),
        'image/object/bbox/xmin': dataset_util.float_list_feature(xmins),
        'image/object/bbox/xmax': dataset_util.float_list_feature(xmaxs),
        'image/object/bbox/ymin': dataset_util.float_list_feature(ymins),
        'image/object/bbox/ymax': dataset_util.float_list_feature(ymaxs),
        'image/object/class/text': dataset_util.bytes_list_feature(classes_text),
        'image/object/class/label': dataset_util.int64_list_feature(classes),
    }))
    return tf_example

def Df2TFrecord(df, imagecolumn, outpath):
    if imagecolumn is 'page_path':
        prefix = ''

    writer = tf.io.TFRecordWriter(outpath)
    grouped = split(df, imagecolumn)
    #print(grouped)

    for group in grouped:
        if imagecolumn is 'figure_path':
        
            tf_example = create_tf_example_figure(group,  outpath)
            writer.write(tf_example.SerializeToString())
        if imagecolumn is 'page_path':
            tf_example = create_tf_example_new(group,  outpath)
            writer.write(tf_example.SerializeToString())

    writer.close()

In [ ]:
shutil.copyfile(PAGE_MODEL + LABELS, OUTPATH +'pages_label_map.pbtxt')

mining_pages_detections = figures_step3.append(bestpages)
mining_pages_detections2 = mining_pages_detections.reindex(axis=0)
pages_grouped = mining_pages_detections2.groupby('catalog_id')

for name, group in pages_grouped:
    imgdir = os.path.join(OUTPATH, name + '_pages/')
    if not os.path.exists(imgdir):
        os.makedirs(imgdir)
    Df2TFrecord(group, 'page_path', OUTPATH + name +'_pages.tfrecord')
    for index, row in group.iterrows():
        imgoutpath = imgdir + os.path.basename(row['page_path'])
        #print(imgoutpath)
        if not os.path.exists(imgoutpath):
            shutil.copyfile(row['page_path'], imgoutpath)

shutil.copyfile(FIGID_MODEL + LABELS, OUTPATH + 'figures_label_map.pbtxt')
figures_step3 = figures_step3[figures_step3.detection_boxes.notnull()]

figures_grouped = figures_step3.groupby('catalog_id')

for name, group in figures_grouped:
    imgdir = os.path.join(OUTPATH, name + '_figures/')
    if not os.path.exists(imgdir):
        os.makedirs(imgdir)
    Df2TFrecord(group, 'figure_path', OUTPATH + name +'_figures.tfrecord')
    for index, row in group.iterrows():
        imgoutpath = imgdir + os.path.basename(str(row['figure_path']))
        #print(imgoutpath)
        if not os.path.exists(imgoutpath):
            shutil.copyfile(row['figure_path'], imgoutpath)
